# Experimenting with least squares and its variants

In [2]:
%matplotlib inline

from sklearn import datasets
from scipy.optimize import fmin_bfgs
import numpy as np
from numpy.linalg import norm
from numpy.linalg import inv

## Data preparation

In [3]:
boston = datasets.load_boston()
data = np.array(boston.data)

The boston dataset is one of the standard regression problems used to experiment with learning algorithms. Below you can find the dataset description

In [4]:
print(boston.DESCR)

.. _boston_dataset:

Boston house prices dataset
---------------------------

**Data Set Characteristics:**  

    :Number of Instances: 506 

    :Number of Attributes: 13 numeric/categorical predictive. Median Value (attribute 14) is usually the target.

    :Attribute Information (in order):
        - CRIM     per capita crime rate by town
        - ZN       proportion of residential land zoned for lots over 25,000 sq.ft.
        - INDUS    proportion of non-retail business acres per town
        - CHAS     Charles River dummy variable (= 1 if tract bounds river; 0 otherwise)
        - NOX      nitric oxides concentration (parts per 10 million)
        - RM       average number of rooms per dwelling
        - AGE      proportion of owner-occupied units built prior to 1940
        - DIS      weighted distances to five Boston employment centres
        - RAD      index of accessibility to radial highways
        - TAX      full-value property-tax rate per $10,000
        - PTRATIO  pu

First step to apply the formulae we learnt during the lectures is to rewrite the dataset in homogeneous coordinates (i.e., we append a column of 1 to the matrix containing the examples):

In [5]:
t = np.ones(len(data)).reshape(len(data),1)
data = np.append(data, t, 1)
target = np.array(boston.target)

array([[1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],
       [1.],

We now divide the data into a training set $X$ and a test set $X_\textrm{test}$.

In [6]:
X,y = data[0:400,:], target[0:400]
X_test, y_test = data[400:,:], target[400:]

# Exercise

1. Calculate the least square solution (to the regression problem outlined above) and evaluate its performances on the training set and on the test set.
1. Calculate the ridge regression solution (set lambda to 0.01) and evaluate its performances on the training set and on test set.
1. Calculate the lasso regression solution and evaluate its performances on the training set and on the test set.

## Notes

- Here it follows a list of functions you may want to use (the required packages are already imported at the beginning of this notebook) along with a very brief explanation of their purpose (`help(nomefun)` will provide you more information about function `nomefun`):
    - `transpose`: matrix transposition (e.g., `transpose(X)`)
    - `dot`: matrix multiplication (e.g., `X.dot(X2)`) 
    - `inv`: matrix inversion (e.g., `inv(X)`)
- to solve the lasso problem you will need to perform a numerical minimization of the associated loss function (as you know, a closed form solution does not exist). There are many numerical optimization algorithms available in the scipy package. My suggestion is to use `fmin_bfgs`. Here it follows an example of how to use it:
    ```python
        def f(w):
            return w[0]**2 + w[1]**2 + w[0] + w[1]
        
        w = fmin_bfgs(f, [0,0])
    ```
    note that the function may (and should) reference your data variables (i.e., $X$ and $y$).
- to evaluate the performances of your solutions use the $S$ statistic:
    $$
        S =  \sqrt{ \frac{1}{n} \sum_{i=1}^n (y_i' - y_i)^2 }
    $$
    where $y'_i$ is your model prediction for the i-th example, and $n$ is the number of examples.

In [65]:
import math

In [66]:
def least_squares(X, y):
    return inv(np.transpose(X).dot(X)).dot(np.transpose(X)).dot(y)

In [67]:
def ridge_regression(X, y, lam):
    return inv(np.transpose(X).dot(X) + np.identity(len(X[0])).dot(lam)).dot(np.transpose(X)).dot(y)

In [83]:
def lasso(w, X, y, lam):
    return np.transpose(y - X.dot(w)).dot(y - X.dot(w)) + lam * sum(w)

In [79]:
def lasso_regression(X, y, lam):
    return fmin_bfgs(lasso, np.zeros(len(X[0])), args = (X, y, lam))

In [70]:
def s_statistics(actual, predicted):
    return math.sqrt(sum([(predicted[i] - actual[i])**2 for i in range(len(actual))]) / len(actual))

In [80]:
def predict(X, w):
    return X.dot(w)

In [89]:
w_least = least_squares(X, y)
w_ridge = ridge_regression(X, y, 0.01)
w_lasso = lasso_regression(X, y, 0.01)
print("Least squares training set s statistics:", s_statistics(y, predict(X, w_least)))
print("Least squares test set s statistics:", s_statistics(y_test, predict(X_test, w_least)))
print("Ridge regression training set s statistics:", s_statistics(y, predict(X, w_ridge)))
print("Ridge regression test set s statistics:", s_statistics(y_test, predict(X_test, w_ridge)))
print("Lasso regression training set s statistics:", s_statistics(y, predict(X, w_lasso)))
print("Lasso regression test set s statistics:", s_statistics(y_test, predict(X_test, w_lasso)))

         Current function value: 8922.270593
         Iterations: 19
         Function evaluations: 577
         Gradient evaluations: 36
Least squares training set s statistics: 4.7228408383263805
Least squares test set s statistics: 6.155792280414106
Ridge regression training set s statistics: 4.7228952650983205
Ridge regression test set s statistics: 6.141787930906379
Lasso regression training set s statistics: 4.722840843957779
Lasso regression test set s statistics: 6.1558291277697
